# Process Data

The purpose of this `.ipynb` is to process `imu.csv` data to get `pitch`, and combine this with `gaze_positions.csv` to get `elevation`, and combine `pitch` with `elevation` to get `gaze angle`. 

## Steps
1. Establish target directory (under `data/`, select folder for session: `session_XX` where XX is a two-digit number).
2. Load `imu.csv` and `gaze_positions.csv` into dataframes.
3. Combine `pitch` with `elevation` to get `gaze angle`.
4. Save processed data to new CSV file (time step + gaze angle), as `gaze_angle.csv`.


In [1]:
import pandas as pd
import plotly.express as px
from scipy.signal import butter, filtfilt, find_peaks
import numpy as np


# if we want to save the output file here from "Run All", make SAVE_OUTPUT = True
SAVE_OUTPUT = True

In [2]:
# LOAD STAIR CONDITION
print("LOAD STAIR")
#  1: Establish target directory 

COND_ID = 'stair-condition'

#target_dir = '/Users/trentonwirth/Desktop/stair-hill_experiment/s2/s2_stair-condition-2025-11-13_03-24-05-4dcbe539/neon_player/exports/000_s2_stair-condition'
target_dir = '/Users/trentonwirth/Desktop/stair-hill_experiment/s3/s3_stair-condition-2025-11-13_03-38-01-99495929/neon_player/exports/000_s3_stair-condition'

if target_dir:
    print(target_dir)
else: 
    print('Target directory doesn not exist')

LOAD STAIR
/Users/trentonwirth/Desktop/stair-hill_experiment/s3/s3_stair-condition-2025-11-13_03-38-01-99495929/neon_player/exports/000_s3_stair-condition


In [7]:
# LOAD HILL CONDITION
print("LOAD HILL")
#  1: Establish target directory 

COND_ID = 'hill-condition'

#target_dir = '/Users/trentonwirth/Desktop/stair-hill_experiment/s2/s2_hill-condition_2025-11-13_03-57-47-e10913da/neon_player/exports/000_s2_hill-condition'
target_dir = '/Users/trentonwirth/Desktop/stair-hill_experiment/s3/s3_hill-condition-2025-11-13_04-07-47-fba7e068/neon_player/exports/000_s3_hill-condition'

if target_dir:
    print(target_dir)
else: 
    print('Target directory doesn not exist')

LOAD HILL
/Users/trentonwirth/Desktop/stair-hill_experiment/s3/s3_hill-condition-2025-11-13_04-07-47-fba7e068/neon_player/exports/000_s3_hill-condition


In [8]:
# 2. Load in csv's

# Load IMU data
imu_df = pd.read_csv(f'{target_dir}/imu.csv')
# Load gaze positions data
gaze_df = pd.read_csv(f'{target_dir}/gaze_positions.csv')

print("IMU data head:")
print(imu_df.head())
print("\nGaze positions data head:")
print(gaze_df.head())

IMU data head:
        timestamp [ns]  gyro x [deg/s]  gyro y [deg/s]  gyro z [deg/s]  \
0  1762981668783083151       -2.956390       -0.019073       -0.501633   
1  1762981668792836151       -2.040863       -0.080109       -0.745773   
2  1762981668802589151       -1.670837        0.102997       -0.627518   
3  1762981668812342151       -0.820160        0.652313       -0.501633   
4  1762981668821796151       -0.879288        0.833511       -0.684738   

   acceleration x [G]  acceleration y [G]  acceleration z [G]  roll [deg]  \
0           -0.006836           -0.056763            0.993530    0.420239   
1            0.001465           -0.061646            1.011108    0.415121   
2            0.004395           -0.064087            1.011597    0.411691   
3            0.000488           -0.062622            1.002319    0.408705   
4            0.015625           -0.062622            0.995483    0.405817   

   pitch [deg]   yaw [deg]  quaternion w  quaternion x  quaternion y  \
0    

In [9]:
# Downsample gaze data to IMU frame rate: for each IMU frame, find the nearest gaze elevation
imu_df_sorted = imu_df.sort_values('timestamp [ns]')
gaze_df_sorted = gaze_df.sort_values('timestamp [ns]')
merged_df = pd.merge_asof(
    imu_df_sorted,
    gaze_df_sorted[['timestamp [ns]', 'elevation [deg]']],
    on='timestamp [ns]',
    direction='nearest'
    # Optionally, set a tolerance to restrict matching distance
    # tolerance=10000  # e.g., 10,000 ns = 0.01 ms
)

# If no gaze frame is close enough, elevation will be NaN
# merged_df = merged_df.dropna(subset=['elevation [deg]'])
# merged_df = merged_df.fillna({'elevation [deg]': 0})
# Uncomment above as needed

# Now, merged_df has IMU frames with nearest gaze elevation
# Calculate gaze angle
merged_df['gaze angle [deg]'] = merged_df['pitch [deg]'] + merged_df['elevation [deg]']
gaze_angle_df = merged_df[['timestamp [ns]', 'gaze angle [deg]']].copy()
# Include pitch and elevation in final df for saving
gaze_angle_df.loc[:, 'pitch [deg]'] = merged_df['pitch [deg]']
gaze_angle_df.loc[:, 'elevation [deg]'] = merged_df['elevation [deg]']
print(f"Size of dataframe: {len(merged_df)}")
print(gaze_angle_df.head())

Size of dataframe: 62597
        timestamp [ns]  gaze angle [deg]  pitch [deg]  elevation [deg]
0  1762981668783083151         -4.230753    -3.765576        -0.465177
1  1762981668792836151         -4.191849    -3.785267        -0.406582
2  1762981668802589151         -3.837434    -3.801966        -0.035469
3  1762981668812342151         -3.789845    -3.806406         0.016562
4  1762981668821796151         -3.639319    -3.810219         0.170899


In [10]:
# Calculate time in seconds, first frame is 0
gaze_angle_df = gaze_angle_df.copy()
start_ns = gaze_angle_df['timestamp [ns]'].iloc[0]
gaze_angle_df['time_sec'] = (gaze_angle_df['timestamp [ns]'] - start_ns) / 1e9

fig = px.scatter(
    gaze_angle_df,
    x='time_sec',
    y='gaze angle [deg]',
    title=f'Gaze Angle Over Time -- {COND_ID}',
    labels={'gaze angle [deg]': 'Gaze Angle (deg) ', 'time_sec': 'Time (sec)'},
    render_mode='webgl'
)
fig.update_traces(mode='lines+markers')
fig.update_yaxes(range=[-90, 45])
fig.show()

In [7]:
# A seconds to minutes fnction because I'm tired

input_seconds = 400

def seconds_to_mss(total_seconds):
    minutes = total_seconds // 60
    seconds = total_seconds % 60
    return f"{minutes}:{seconds:02d}"

# Example

print(seconds_to_mss(input_seconds))  # Output: 10:11

6:40


In [8]:
# Histogram of gaze angle (uses existing `gaze_angle_df` and `COND_ID`)
ga = gaze_angle_df['gaze angle [deg]']
mean_ga = ga.mean()
std_ga = ga.std()

fig = px.histogram(
    gaze_angle_df,
    x='gaze angle [deg]',
    nbins=60,
    title=f'Histogram of Gaze Angle -- {COND_ID}',
    labels={'gaze angle [deg]': 'Gaze Angle (deg)'},
    marginal='box',
    template='plotly_white'
)
fig.update_layout(bargap=0.02)

# Fix x-axis range to [-80, 20]
fig.update_xaxes(range=[-80, 20])

# Add mean and ±1σ lines
fig.add_vline(x=mean_ga, line=dict(color='red', width=2), annotation_text=f"mean={mean_ga:.2f}", annotation_position="top right")
fig.add_vline(x=mean_ga - std_ga, line=dict(color='orange', width=1, dash='dash'), annotation_text=f"-1σ", annotation_position="top left")
fig.add_vline(x=mean_ga + std_ga, line=dict(color='orange', width=1, dash='dash'), annotation_text=f"+1σ", annotation_position="top left")

fig.show()

In [9]:
def detect_gait_events(imu_df, acc_col='acceleration z [G]',
                       low=0.5, high=8.0,
                       min_step_time=0.3,
                       prominence=0.02):
    imu_df = imu_df.copy()
    start_ns = imu_df['timestamp [ns]'].iloc[0]
    imu_df['time_sec'] = (imu_df['timestamp [ns]'] - start_ns) / 1e9

    timestamps = imu_df['timestamp [ns]'].values.astype(np.float64)
    dt = np.diff(timestamps) / 1e9
    fs = 1.0 / np.median(dt)

    acc = imu_df[acc_col].values
    b, a = butter(4, [low / (fs / 2.0), high / (fs / 2.0)], btype="band")
    acc_filt = filtfilt(b, a, acc)
    imu_df['acc_filt'] = acc_filt

    min_distance_samples = int(min_step_time * fs)

    hs_idx, _ = find_peaks(
        acc_filt,
        prominence=prominence,
        distance=min_distance_samples
    )
    to_idx, _ = find_peaks(
        -acc_filt,
        prominence=prominence,
        distance=min_distance_samples
    )

    hs_times = imu_df.loc[hs_idx, 'time_sec'].to_numpy()
    to_times = imu_df.loc[to_idx, 'time_sec'].to_numpy()

    return {
        "imu_df": imu_df,
        "fs": fs,
        "hs_idx": hs_idx,
        "to_idx": to_idx,
        "hs_times": hs_times,
        "to_times": to_times,
    }

# Example use:
events = detect_gait_events(imu_df)
hs_times = events["hs_times"]
to_times = events["to_times"]

In [ ]:
import plotly.express as px

# Use the imu_df that has time_sec + acc_filt from detect_gait_events
imu_plot_df = events["imu_df"].copy()

fig = px.scatter(
    imu_plot_df,
    x="time_sec",
    y="acc_filt",
    title=f"Filtered IMU Vertical Acceleration Over Time -- {COND_ID}",
    labels={
        "acc_filt": "Vertical Acceleration (G, filtered)",
        "time_sec": "Time (sec)",
    },
    render_mode="webgl",
)

fig.update_traces(mode="lines+markers")

# Optional: set a y-range if you want to constrain the view
# fig.update_yaxes(range=[-1.5, 1.5])

# --- Add vertical lines for heel-strike (red) and toe-off (blue) ---

y_min = imu_plot_df["acc_filt"].min()
y_max = imu_plot_df["acc_filt"].max()

shapes = []

# Heel-strike (red)
for t in hs_times:
    shapes.append({
        "type": "line",
        "xref": "x",
        "yref": "y",
        "x0": t,
        "x1": t,
        "y0": y_min,
        "y1": y_max,
        "line": {"width": 2, "color": "red"},
        "opacity": 0.7,
    })

# Toe-off (blue)
for t in to_times:
    shapes.append({
        "type": "line",
        "xref": "x",
        "yref": "y",
        "x0": t,
        "x1": t,
        "y0": y_min,
        "y1": y_max,
        "line": {"width": 2, "color": "blue"},
        "opacity": 0.7,
    })

fig.update_layout(shapes=shapes)

fig.show()

In [11]:
np.shape(hs_times), np.shape(to_times)

((1103,), (1183,))

In [ ]:
import plotly.express as px

# Calculate time in seconds, first frame is 0
gaze_angle_df = gaze_angle_df.copy()
start_ns = gaze_angle_df['timestamp [ns]'].iloc[0]
gaze_angle_df['time_sec'] = (gaze_angle_df['timestamp [ns]'] - start_ns) / 1e9

fig = px.scatter(
    gaze_angle_df,
    x='time_sec',
    y='gaze angle [deg]',
    title=f'Gaze Angle Over Time -- {COND_ID}',
    labels={'gaze angle [deg]': 'Gaze Angle (deg) ', 'time_sec': 'Time (sec)'},
    render_mode='webgl'
)
fig.update_traces(mode='lines+markers')
fig.update_yaxes(range=[-90, 45])

# After you create `fig` and before fig.show()

y_min = gaze_angle_df['gaze angle [deg]'].min()
y_max = gaze_angle_df['gaze angle [deg]'].max()

shapes = []

# Red = heel-strike
for t in hs_times:
    shapes.append({
        "type": "line",
        "xref": "x",
        "yref": "y",
        "x0": t,
        "x1": t,
        "y0": y_min,
        "y1": y_max,
        "line": {"width": 2, "color": "red"},
        "opacity": 0.7,
    })

# Blue = toe-off
for t in to_times:
    shapes.append({
        "type": "line",
        "xref": "x",
        "yref": "y",
        "x0": t,
        "x1": t,
        "y0": y_min,
        "y1": y_max,
        "line": {"width": 2, "color": "blue"},
        "opacity": 0.7,
    })

fig.update_layout(shapes=shapes)
fig.show()

In [11]:
from ipywidgets import widgets
from IPython.display import display

gaze_angle_df.head()
import plotly.graph_objects as go

def plot_gaze_metric(metric):
    fig2 = go.Figure()
    fig2.add_trace(go.Scatter(
        x=gaze_angle_df['time_sec'],
        y=gaze_angle_df[metric],
        mode='lines+markers',
        name=metric,
        line=dict(width=2),
        marker=dict(size=4)
    ))
    fig2.update_layout(
        title=f'{metric} Over Time',
        xaxis_title='Time (sec)',
        yaxis_title=f'{metric}',
        yaxis=dict(range=[-90, 45] if metric in ['gaze angle [deg]', 'elevation [deg]', 'pitch [deg]'] else None)
    )
    fig2.show()

dropdown = widgets.Dropdown(
    options=['elevation [deg]', 'pitch [deg]'],
    value='elevation [deg]',
    description='Metric:',
    disabled=False,
)

widgets.interact(plot_gaze_metric, metric=dropdown)

interactive(children=(Dropdown(description='Metric:', options=('elevation [deg]', 'pitch [deg]'), value='eleva…

<function __main__.plot_gaze_metric(metric)>

In [14]:
# Save entire gaze_angle_df to CSV in the target directory

if SAVE_OUTPUT == True:
    out_path = f'{target_dir}/gaze_angle.csv'
    gaze_angle_df.to_csv(out_path, index=False)
    print(f"Saved {len(gaze_angle_df)} rows to {out_path}")
else: 
    print("No output is being saved")


Saved 62597 rows to /Users/trentonwirth/Desktop/stair-hill_experiment/s3/s3_hill-condition-2025-11-13_04-07-47-fba7e068/neon_player/exports/000_s3_hill-condition/gaze_angle.csv
